## RQ2: Asynchronous duet overlaps

In [20]:
%load_ext autoreload
%autoreload 2

import plotly.express as px
import pandas as pd
import numpy as np
from scipy.stats import (
    bootstrap,
    gmean,
)
from IPython.display import display

from duet.process import *
from duet.constants import *
from common import *

df_prep = preprocess_data(load_raw())
unique_suites = df_prep[RF.suite].unique()

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


/Users/tdrozdik/school/asynchronous-duet/duet/process.py:426: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Compute overlaps using different values of `minimum_overlap_ratio`

In [30]:
iter_overlap_pair_dfs = []

df_prep_overlaps = compute_overlaps(df_prep)
df_prep_overlaps[DF.overlap_rate] = None
iter_overlap_pair_dfs.append((df_prep_overlaps, df_prep))

for overlap_ratio in np.arange(0.1, 1, 0.2):
    df_prep_overlaps_prep = preprocess_overlaps(df_prep_overlaps, p=overlap_ratio)
    df_prep_overlaps_prep[DF.overlap_rate] = str(
        round(overlap_ratio, 1)
    )  # assign as string to make it categorical
    iter_overlap_pair_dfs.append((df_prep_overlaps_prep, df_prep))

df_over = pd.concat([pair[0] for pair in iter_overlap_pair_dfs])
display(df_over)

# Aggregate the results
def aggregate_size_and_time(df_over, df_iter):
    """Compute iteration/overlap aggregate count and total time"""
    df_over_agg = (
        df_over.groupby(BENCHMARK_ENV_COL + [DF.overlap_rate])
        .agg(
            overlap_count=(RF.overlap_time_ns, np.size),
            total_overlap_time=(RF.overlap_time_ns, np.sum),
        )
        .reset_index()
    )

    df_iter_agg = df_iter.groupby(BENCHMARK_ENV_COL).agg(
        iteration_count=(RF.time_ns, np.size), total_iteration_time=(RF.time_ns, np.sum)
    )
    # Total iteration time is doubled because of duet run thus halve it
    df_iter_agg["total_iteration_time"] = df_iter_agg["total_iteration_time"] / 2

    return df_over_agg.merge(df_iter_agg, on=BENCHMARK_ENV_COL).reset_index(drop=True)


df_over_agg = pd.concat(
    [
        aggregate_size_and_time(df_overlaps, df_iters)
        for df_overlaps, df_iters in iter_overlap_pair_dfs
    ]
)
display(df_over_agg)

/var/folders/w9/dv48b_r16kb5ms8fbd38w7dr0000gp/T/ipykernel_48179/4165084439.py:9: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



index benchmark  total_ms  iteration_time_ns_A  process_cpu_time_ns  \
0        83313    avrora  153801.0         6.217814e+09         5.730000e+09   
1        83313    avrora  153801.0         6.217814e+09         5.730000e+09   
2        83314    avrora  161246.0         7.409581e+09         6.190000e+09   
3        83314    avrora  161246.0         7.409581e+09         6.190000e+09   
4        83315    avrora  167929.0         6.670759e+09         5.670000e+09   
...        ...       ...       ...                  ...                  ...   
177059  138165  557_xz_r       NaN         3.848540e+11                  NaN   
177061  138166  557_xz_r       NaN         3.855060e+11                  NaN   
177063  138167  557_xz_r       NaN         3.855852e+11                  NaN   
177065  138168  557_xz_r       NaN         3.841578e+11                  NaN   
177067  138169  557_xz_r       NaN         3.839167e+11                  NaN   

        compilation_time_ms  compilation_total_ms  \
0                      64.0                6596.0   
1                      64.0                6596.0   
2                      67.0                6663.0   
3                      67.0                6663.0   
4                      81.0                6745.0   
...                     ...                   ...   
177059                  NaN                   NaN   
177061                  NaN                   NaN   
177063                  NaN                   NaN   
177065                  NaN                   NaN   
177067                  NaN                   NaN   

        jmx_memory_young_collection_count  jmx_memory_young_collection_delta  \
0                                    21.0                                0.0   
1                                    21.0                                0.0   
2                                    22.0                                0.0   
3                                    22.0                                0.0   
4                                    23.0                                0.0   
...                                   ...                                ...   
177059                                NaN                                NaN   
177061                                NaN                                NaN   
177063                                NaN                                NaN   
177065                                NaN                                NaN   
177067                                NaN                                NaN   

        jmx_memory_young_collection_total_ms  ...  iteration_time  \
0                                       51.0  ...               6   
1                                       51.0  ...               6   
2                                       53.0  ...               7   
3                                       53.0  ...               7   
4                                       54.0  ...               6   
...                                      ...  ...             ...   
177059                                   NaN  ...             384   
177061                                   NaN  ...             385   
177063                                   NaN  ...             385   
177065                                   NaN  ...             384   
177067                                   NaN  ...             383   

        environment  iteration_time_ns_B  iteration_B  iteration_start_ns_B  \
0          teaching         5.969598e+09           21          1.670570e+18   
1          teaching         7.647649e+09           22          1.670570e+18   
2          teaching         7.647649e+09           22          1.670570e+18   
3          teaching         6.695232e+09           23          1.670570e+18   
4          teaching         6.695232e+09           23          1.670570e+18   
...             ...                  ...          ...                   ...   
177059   bare-metal         3.859845e+11            4          1.655

suite        benchmark  type    environment minumum_overlap_ratio  \
0     dacapo           avrora  duet  AWS:t3.medium                   0.1   
1     dacapo           avrora  duet     bare-metal                   0.1   
2     dacapo           avrora  duet       teaching                   0.1   
3     dacapo              fop  duet  AWS:t3.medium                   0.1   
4     dacapo              fop  duet     bare-metal                   0.1   
..       ...              ...   ...            ...                   ...   
189  speccpu  549_fotonik3d_r  duet     bare-metal                   0.9   
190  speccpu       554_roms_r  duet  AWS:t3.medium                   0.9   
191  speccpu       554_roms_r  duet     bare-metal                   0.9   
192  speccpu         557_xz_r  duet  AWS:t3.medium                   0.9   
193  speccpu         557_xz_r  duet     bare-metal                   0.9   

     overlap_count  total_overlap_time  iteration_count  total_iteration_time  
0            914.0        3.165725e+12             1117          3.297613e+12  
1           1996.0        3.911042e+12             2448          4.011097e+12  
2            353.0        1.422068e+12              428          1.496580e+12  
3            867.0        2.370359e+11             1144          2.811878e+11  
4           1817.0        1.299560e+11             2448          1.563040e+11  
..             ...                 ...              ...                   ...  
189          160.0        6.647522e+13              320          6.656336e+13  
190           66.0        3.191624e+13              132          3.196060e+13  
191          232.0        5.496767e+13              464          5.582892e+13  
192           44.0        2.980122e+13               88          2.991175e+13  
193          172.0        6.532772e+13              344          6.595711e+13  

[974 rows x 9 columns]

In [31]:
import plotly.graph_objects as go

df_over_agg["relative_overlap_time"] = (
    df_over_agg["total_overlap_time"] / df_over_agg["total_iteration_time"]
)
px.box(
    df_over_agg,
    x=DF.overlap_rate,
    y="relative_overlap_time",
    color=RF.suite,
    facet_col=DF.env,
    hover_data=[RF.benchmark],
)

In [32]:
for suite in unique_suites:
    # Absolute overlap count by preprocessing level
    fig = px.bar(
        df_over_agg[df_over_agg[RF.suite] == suite],
        x=RF.benchmark,
        y="overlap_count",
        color=DF.overlap_rate,
        facet_col=DF.env,
        barmode="group",
        title=f"Overlap count by preprocessing levels - {suite}",
    )
    fig.update_xaxes(categoryorder="category ascending")
    fig.show()

    # Relative overlap count to total iterations per preprocessing level
    df_over_agg["relative_overlap_count"] = (
        df_over_agg["overlap_count"] / df_over_agg["iteration_count"]
    )
    fig = px.bar(
        df_over_agg[df_over_agg[RF.suite] == suite],
        x=RF.benchmark,
        y="relative_overlap_count",
        color=DF.overlap_rate,
        facet_col=DF.env,
        barmode="group",
        title=f"Overlap count relative to total iterations by preprocessing levels - {suite}",
    )
    fig.update_xaxes(categoryorder="category ascending")
    fig.show()

    # Relative overlap count to total iterations per preprocessing level
    df_over_agg["relative_overlap_time"] = (
        df_over_agg["total_overlap_time"] / df_over_agg["total_iteration_time"]
    )
    fig = px.bar(
        df_over_agg[df_over_agg[RF.suite] == suite],
        x=RF.benchmark,
        y="relative_overlap_time",
        color=DF.overlap_rate,
        facet_col=DF.env,
        barmode="group",
        title=f"Overlap time relative to total iteration time by preprocessing levels - {suite}",
    )
    fig.update_xaxes(categoryorder="category ascending")
    fig.show()

    # Distribution of overlap times per preprocessing level
    fig = px.strip(
        df_over[(df_over[RF.suite] == suite) & (df_over[DF.overlap_rate] == "0.5")],
        x=RF.overlap_time_ns,
        y=RF.benchmark,
        color=DF.overlap_rate,
        facet_col=DF.env,
        # points="outliers",
        orientation="h",
        title=f"Overlap time: {suite}",
    )
    fig.update_layout(height=1000)
    fig.update_yaxes(categoryorder="category descending")
    fig.show()